# Retrieval - 1st attempt

# Set up

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from loguru import logger
import json

import sys
sys.path.insert(0, '..')

In [3]:
import os

from tqdm.notebook import tqdm
import pandas as pd

In [4]:
import nest_asyncio

nest_asyncio.apply()

In [5]:
from dotenv import load_dotenv

load_dotenv()

True

# Arguments

In [6]:
from src.run.args import RunInputArgs

ARGS = RunInputArgs(
    EXPERIMENT_NAME="Review Rec Bot - Yelp Review Rec Bot",
    RUN_NAME="005_use_smaller_embedding_model",
    RUN_DESCRIPTION="""
# Retriever - Smaller embedding model to avoid GPU OOM

## Changelog
Compared to 004:
- Use Snowflake/snowflake-arctic-embed-m-v1.5 according to a 1/3 size but better retrieval performance
- Ref: https://huggingface.co/spaces/mteb/leaderboard
""",
    TESTING=False,
    LOG_TO_MLFLOW=True,
    OBSERVABILITY=True,
    RECREATE_INDEX=True,
    RECREATE_RETRIEVAL_EVAL_DATASET=True,
    RECREATE_RESPONSE_EVAL_DATASET=True,
    DEBUG=True,
)

ARGS

{
  "EXPERIMENT_NAME": "Review Rec Bot - Yelp Review Rec Bot",
  "RUN_NAME": "005_use_smaller_embedding_model",
  "RUN_DESCRIPTION": "\n# Retriever - Smaller embedding model to avoid GPU OOM\n\n## Changelog\nCompared to 004:\n- Use Snowflake/snowflake-arctic-embed-m-v1.5 according to a 1/3 size but better retrieval performance\n- Ref: https://huggingface.co/spaces/mteb/leaderboard\n",
  "TESTING": false,
  "DEBUG": true,
  "OBSERVABILITY": true,
  "LOG_TO_MLFLOW": true,
  "RECREATE_INDEX": true,
  "RECREATE_RETRIEVAL_EVAL_DATASET": true,
  "RECREATE_RESPONSE_EVAL_DATASET": true
}

# Load config

In [7]:
from src.run.cfg import RunConfig

In [8]:
cfg = RunConfig()
cfg.init(ARGS)

2024-08-05 23:43:39.459 | INFO     | src.run.cfg:init:123 - Starting Observability server with Phoenix...
INFO:phoenix.config:📋 Ensuring phoenix working directory: /home/dvquys/.phoenix


🌍 To view the Phoenix app in your browser, visit http://localhost:6006/
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix


2024-08-05 23:43:45.322 | INFO     | src.run.cfg:init:132 - Enabling LlamaIndex DEBUG logging...
2024-08-05 23:43:45.323 | INFO     | src.run.cfg:init:141 - Setting up MLflow experiment Review Rec Bot - Yelp Review Rec Bot - run 005_use_smaller_embedding_model...
2024-08-05 23:43:45.546 | INFO     | src.run.cfg:init:150 - Notebook-generated artifacts are persisted at data/005_use_smaller_embedding_model
2024-08-05 23:43:45.547 | INFO     | src.run.cfg:init:156 - ARGS.RECREATE_INDEX=True -> Overwriting db_collection and nodes_persist_fp...


In [9]:
cfg

/home/dvquys/frostmourne/study/vietai-genai03/final-project/review-rec-bot/.venv/lib/python3.11/site-packages/pydantic/main.py:364: UserWarning: Pydantic serializer warnings:
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  return self.__pydantic_serializer__.to_python(


{
  "args": {
    "EXPERIMENT_NAME": "Review Rec Bot - Yelp Review Rec Bot",
    "RUN_NAME": "005_use_smaller_embedding_model",
    "RUN_DESCRIPTION": "\n# Retriever - Smaller embedding model to avoid GPU OOM\n\n## Changelog\nCompared to 004:\n- Use Snowflake/snowflake-arctic-embed-m-v1.5 according to a 1/3 size but better retrieval performance\n- Ref: https://huggingface.co/spaces/mteb/leaderboard\n",
    "TESTING": false,
    "DEBUG": true,
    "OBSERVABILITY": true,
    "LOG_TO_MLFLOW": true,
    "RECREATE_INDEX": true,
    "RECREATE_RETRIEVAL_EVAL_DATASET": true,
    "RECREATE_RESPONSE_EVAL_DATASET": true
  },
  "app_name": "review_rec_bot",
  "db_collection": "review_rec_bot__huggingface__Snowflake_snowflake_arctic_embed_m_v1_5__005_use_smaller_embedding_model",
  "nodes_persist_fp": "data/005_use_smaller_embedding_model/nodes.pkl",
  "notebook_cache_dp": "data/005_use_smaller_embedding_model",
  "data_fp": "../data/yelp_dataset/sample/sample_100_biz/denom_review.parquet",
  "llm_

## Set up logger to collect additional info

In [10]:
collect_fp = f"{cfg.notebook_cache_dp}/collect.log"
logger.add(collect_fp, filter=lambda record: "[COLLECT]" in record['message'], mode='w')

1

# Load input data

In [11]:
data = pd.read_parquet(cfg.data_fp)
data = data.assign(
    biz_categories=lambda df: df['biz_categories'].str.split(', '),
    date=lambda df: df['date'].dt.strftime('%Y-%m-%dT%H:%M:%S')
)
logger.info(f"[COLLECT] {len(data)=}")
data.iloc[0]

2024-08-05 23:43:45.721 | INFO     | __main__:<module>:6 - [COLLECT] len(data)=5240


review_id                                      L0jv8c2FbpWSlfNC6bbUEA
user_id                                        bFPdtzu11Oi0f92EAcjqmg
business_id                                    IDtLPgUrqorrpqSLdfMhZQ
review_stars                                                        5
useful                                                              0
funny                                                               0
cool                                                                0
text                What a great addition to the Funk Zone!  Grab ...
date                                              2016-10-13T22:50:47
biz_name                                         Helena Avenue Bakery
biz_address                                     131 Anacapa St, Ste C
biz_city                                                Santa Barbara
biz_state                                                          CA
biz_postal_code                                                 93101
biz_latitude        

In [12]:
input_data = data
if ARGS.TESTING:
    input_data = data[:20]
logger.info(f"[COLLECT] {len(input_data)=}")

2024-08-05 23:43:45.749 | INFO     | __main__:<module>:4 - [COLLECT] len(input_data)=5240


In [13]:
input_data.columns

Index(['review_id', 'user_id', 'business_id', 'review_stars', 'useful',
       'funny', 'cool', 'text', 'date', 'biz_name', 'biz_address', 'biz_city',
       'biz_state', 'biz_postal_code', 'biz_latitude', 'biz_longitude',
       'biz_stars', 'biz_review_count', 'biz_is_open', 'biz_attributes',
       'biz_categories', 'biz_hours'],
      dtype='object')

# Prepare documents

In [14]:
from llama_index.core import Document

documents = []
embedding_visible_metadata = ["review_stars", "biz_name", "biz_address", "biz_city", "biz_state", "biz_categories"]
excluded_embed_metadata_keys = [k for k in input_data.columns if k not in embedding_visible_metadata]

for i, row in tqdm(input_data.iterrows(), total=len(input_data)):
    record = row.to_dict()
    text = record['text']
    metadata = {k: v for k, v in record.items() if k not in ('text')}
    
    doc = Document(
        text=text,
        metadata=metadata,
        excluded_embed_metadata_keys=excluded_embed_metadata_keys,
        excluded_llm_metadata_keys=excluded_embed_metadata_keys
    )
    documents.append(doc)

logger.info(f"[COLLECT] {len(documents)=}")

  0%|          | 0/5240 [00:00<?, ?it/s]

2024-08-05 23:43:46.293 | INFO     | __main__:<module>:20 - [COLLECT] len(documents)=5240


#### Check document embedding text

In [15]:
from llama_index.core.schema import MetadataMode

In [16]:
document = documents[0]
print(document.get_content(metadata_mode=MetadataMode.EMBED))

review_stars: 5
biz_name: Helena Avenue Bakery
biz_address: 131 Anacapa St, Ste C
biz_city: Santa Barbara
biz_state: CA
biz_categories: ['Food', 'Restaurants', 'Salad', 'Coffee & Tea', 'Breakfast & Brunch', 'Sandwiches', 'Bakeries']

What a great addition to the Funk Zone!  Grab a bite, grab some tastings, life is good. Right next door to the Santa Barbara Wine Collective, in fact it actually shares the same tables.  We had a fabulous savory croissant.


# Set up LLM

In [18]:
llm, embed_model = cfg.setup_llm()

modules.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/253 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/243k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/54.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/738 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/297 [00:00<?, ?B/s]

In [19]:
print(cfg.llm_cfg.model_dump_json(indent=2))

{
  "llm_provider": "togetherai",
  "llm_model_name": "meta-llama/Meta-Llama-3.1-8B-Instruct-Turbo",
  "embedding_provider": "huggingface",
  "embedding_model_name": "Snowflake/snowflake-arctic-embed-m-v1.5",
  "embedding_model_dim": 768,
  "ollama__host": "192.168.100.14",
  "ollama__port": 11434
}


In [20]:
from llama_index.core import Settings
Settings.embed_model = embed_model
Settings.llm = llm

# Vector Store

In [21]:
import qdrant_client
from llama_index.core import VectorStoreIndex
from llama_index.core import StorageContext
from llama_index.vector_stores.qdrant import QdrantVectorStore

from src.run.orchestrator import RunOrchestrator

In [22]:
qdrantdb = qdrant_client.QdrantClient(
    host="localhost",
    port=6333
)
aqdrantdb = qdrant_client.AsyncQdrantClient(
    host="localhost",
    port=6333
)

RunOrchestrator.setup_db(cfg, qdrantdb)

db_collection = qdrantdb.get_collection(cfg.db_collection)
vector_store = QdrantVectorStore(
    client=qdrantdb,
    collection_name=cfg.db_collection,
    aclient=aqdrantdb,
    prefer_grpc=True
)
storage_context = StorageContext.from_defaults(vector_store=vector_store)

2024-08-05 23:46:40.354 | INFO     | src.run.orchestrator:setup_db:26 - Creating new Qdrant collection review_rec_bot__huggingface__Snowflake_snowflake_arctic_embed_m_v1_5__005_use_smaller_embedding_model...


Both client and aclient are provided. If using `:memory:` mode, the data between clients is not synced.


WARNI [llama_index.vector_stores.qdrant.base] Both client and aclient are provided. If using `:memory:` mode, the data between clients is not synced.


# Index Embeddings

In [23]:
import time
import pickle
from multiprocessing import set_start_method
from llama_index.core.node_parser import SemanticSplitterNodeParser
# from llama_index.core.node_parser import SentenceSplitter

In [24]:
chunker = SemanticSplitterNodeParser
chunker_cfg = {
    "buffer_size": 1,
    "breakpoint_percentile_threshold": 95,
    "embed_model": embed_model
}

# chunker = SentenceSplitter
# chunker_cfg = {
#     "chunk_size": 512,
#     "chunk_overlap": 10
# }

In [25]:
t0 = time.perf_counter()
# TODO: TO understand the differences between points_count and indexed_vector_counts.
# Here indexed_vector_counts = 0
db_collection_count = db_collection.points_count

if db_collection_count > 0 and ARGS.RECREATE_INDEX == False:
    logger.info(f"Loading index from existing DB...")
    with open(cfg.nodes_persist_fp, 'rb') as f:
        logger.info(f"Loading cached `nodes` at {cfg.nodes_persist_fp}...")
        nodes = pickle.load(f)
else:
    logger.info(f"Creating new DB index...")
    from llama_index.core.extractors import TitleExtractor
    from llama_index.core.ingestion import IngestionPipeline, IngestionCache

    # create the pipeline with transformations
    pipeline = IngestionPipeline(
        transformations=[
            chunker(**chunker_cfg),
            embed_model,
        ],
        vector_store = vector_store
    )

    num_workers = None
    # TODO: I can get the preprocessing completed much quicker if I push the initial steps through a multiprocessing loop and then separately create the embeddings using the built-in batching already provided in the SentenceTransformer encode method.
    # Ref: https://github.com/run-llama/llama_index/issues/10104#issuecomment-1899401584
    # Currently setting num_workers leads to code simple hang
    # Ref: https://github.com/run-llama/llama_index/issues/10104
    # num_workers = os.cpu_count() - 1
    # os.environ['TOKENIZERS_PARALLELISM'] = 'true'
    # set_start_method("spawn", force=True)  # it hangs without this line
    logger.info(f"Running Ingestion Pipeline with {num_workers=}...")
    nodes = await pipeline.arun(documents=documents, num_workers=num_workers, show_progress=True)
    logger.info(f"Persisting nodes to {cfg.nodes_persist_fp}...")
    with open(cfg.nodes_persist_fp, 'wb') as f:
        pickle.dump(nodes, f)
index = VectorStoreIndex.from_vector_store(vector_store, storage_context=storage_context)
t1 = time.perf_counter()

2024-08-05 23:46:40.888 | INFO     | __main__:<module>:12 - Creating new DB index...
2024-08-05 23:46:40.894 | INFO     | __main__:<module>:33 - Running Ingestion Pipeline with num_workers=None...


Parsing nodes:   0%|          | 0/5240 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/4 [00:00<?, ?it/s]

> Adding chunk: What a great addition to the Funk Zone!  Grab a...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: What a great addition to the Funk Zone!  Grab a...


...

Generating embeddings:   0%|          | 0/10 [00:00<?, ?it/s]

> Adding chunk: The ice cream du jour downtown was busy but a t...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: The ice cream du jour downtown was busy but a t...


> Adding chunk: I actually liked the truffle even better than m...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I actually liked the truffle even better than m...
Generating embeddings: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1022/1022 [03:42<00:00,  4.60it/s]
2024-08-05 23:55:39.264 | INFO     | __main__:<module>:35 - Persisting nodes to data/005_use_smaller_embedding_model/nodes.pkl...


In [26]:
logger.info(f"Indexing {len(documents)} into VectorStoreIndex took {t1 - t0:,.0f}s")
logger.info(f"[COLLECT] {len(nodes)=}")

2024-08-05 23:55:41.169 | INFO     | __main__:<module>:1 - Indexing 5240 into VectorStoreIndex took 540s
2024-08-05 23:55:41.170 | INFO     | __main__:<module>:2 - [COLLECT] len(nodes)=10219


# Analyze Chunks

In [27]:
for i, node in enumerate(nodes[:5]):
    print(f"\n\n==========Node {i+1}============")
    print(node.metadata)
    print(node.get_text())



==========Node 1============
{'review_id': 'L0jv8c2FbpWSlfNC6bbUEA', 'user_id': 'bFPdtzu11Oi0f92EAcjqmg', 'business_id': 'IDtLPgUrqorrpqSLdfMhZQ', 'review_stars': 5, 'useful': 0, 'funny': 0, 'cool': 0, 'date': '2016-10-13T22:50:47', 'biz_name': 'Helena Avenue Bakery', 'biz_address': '131 Anacapa St, Ste C', 'biz_city': 'Santa Barbara', 'biz_state': 'CA', 'biz_postal_code': '93101', 'biz_latitude': 34.4144445, 'biz_longitude': -119.6906718, 'biz_stars': 4.0, 'biz_review_count': 389, 'biz_is_open': 1, 'biz_attributes': {'AcceptsInsurance': None, 'Alcohol': "u'none'", 'Ambience': "{'touristy': False, 'hipster': True, 'romantic': False, 'divey': False, 'intimate': False, 'trendy': True, 'upscale': False, 'classy': False, 'casual': True}", 'BYOB': None, 'BestNights': None, 'BikeParking': 'True', 'BusinessAcceptsBitcoin': None, 'BusinessAcceptsCreditCards': 'True', 'BusinessParking': "{'garage': False, 'street': True, 'validated': False, 'lot': False, 'valet': False}", 'ByAppointmentOnly':

# Construct Retriever

In [28]:
from llama_index.core.retrievers import VectorIndexRetriever

In [29]:
print(cfg.retrieval_cfg.model_dump_json(indent=2))

{
  "retrieval_top_k": 10,
  "retrieval_similarity_cutoff": null,
  "rerank_top_k": 5,
  "rerank_model_name": "BAAI/bge-reranker-large"
}


In [30]:
# configure retriever
retriever = VectorIndexRetriever(
    index=index,
    similarity_top_k=cfg.retrieval_cfg.retrieval_top_k,
)

## Test retrieval

In [31]:
from llama_index.core.response.notebook_utils import display_source_node

In [32]:
query = "cold brew coffee"
retrieval_results = await retriever.aretrieve(query)
for node in retrieval_results:
    display_source_node(node, source_length=1000)
    print(node.get_content(metadata_mode=MetadataMode.EMBED))
    print("\n")

> Top 10 nodes:
> [Node 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8] [Similarity score:             0.519297] Will definitely order from here again!
> [Node cdb1fa8b-c59f-4297-b6ad-d535e5de8ceb] [Similarity score:             0.517871] I went here today for my first time and recieved outstanding service, great food, and ice cold be...
> [Node bf0d0553-8994-40e7-af47-b3f8d2c3559c] [Similarity score:             0.514039] I would recommend this place!
> [Node 044b6706-39a1-41d7-8278-379941271897] [Similarity score:             0.512586] Got try it
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.509811] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.509687] Definitely try this place for yourself
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.507322] !! I might stalk them now
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.507087] We did not complain or

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8] [Similarity score:             0.519297] Will definitely order from here again!
> [Node cdb1fa8b-c59f-4297-b6ad-d535e5de8ceb] [Similarity score:             0.517871] I went here today for my first time and recieved outstanding service, great food, and ice cold be...
> [Node bf0d0553-8994-40e7-af47-b3f8d2c3559c] [Similarity score:             0.514039] I would recommend this place!
> [Node 044b6706-39a1-41d7-8278-379941271897] [Similarity score:             0.512586] Got try it
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.509811] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.509687] Definitely try this place for yourself
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.507322] !! I might stalk them now
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:      

**Node ID:** 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8<br>**Similarity:** 0.5192973<br>**Text:** Will definitely order from here again!<br>

review_stars: 5
biz_name: BAP
biz_address: 1224 South St
biz_city: Philadelphia
biz_state: PA
biz_categories: ['Korean', 'Restaurants']

Will definitely order from here again!




**Node ID:** cdb1fa8b-c59f-4297-b6ad-d535e5de8ceb<br>**Similarity:** 0.51787114<br>**Text:** I went here today for my first time and recieved outstanding service, great food, and ice cold beer! The atmosphere was very welcoming as well as our server, Skye!<br>

...

review_stars: 2
biz_name: Bar One
biz_address: 767 S 9th St
biz_city: Philadelphia
biz_state: PA
biz_categories: ['Cocktail Bars', 'Bars', 'Italian', 'Nightlife', 'Restaurants']

We did not complain or say another word. We just packed up and left




**Node ID:** 40696cf7-d98a-493b-9cec-f370aaa96de0<br>**Similarity:** 0.505225<br>**Text:** Cheers!<br>

review_stars: 4
biz_name: Bier Brewery and Tap Room
biz_address: 5133 E 65th St
biz_city: Indianapolis
biz_state: IN
biz_categories: ['Food', 'Beer', 'Wine & Spirits', 'Breweries']

Cheers!




**Node ID:** d9213cd2-1b51-478d-ab29-8d30d1001b40<br>**Similarity:** 0.5021323<br>**Text:** I'll be back again for sure!!!<br>

review_stars: 5
biz_name: BAP
biz_address: 1224 South St
biz_city: Philadelphia
biz_state: PA
biz_categories: ['Korean', 'Restaurants']

I'll be back again for sure!!!




## Retrieval Evaluation

### Synthetic

In [33]:
with open(cfg.nodes_persist_fp, 'rb') as f:
    nodes = pickle.load(f)

In [34]:
from src.run.eval import RetrievalEvaluator

In [35]:
retrieval_evaluator = RetrievalEvaluator()
retrieval_evaluator.generate_synthetic_dataset(cfg, nodes)

2024-08-05 23:58:29.554 | INFO     | src.run.eval.retrieval:generate_synthetic_dataset:36 - Creating new retrieval eval dataset at data/005_use_smaller_embedding_model/retrieval_synthetic_eval_dataset.json...
2024-08-05 23:58:29.555 | INFO     | src.run.eval.retrieval:generate_synthetic_dataset:40 - Sampling 20 nodes for retrieval evaluation...
2024-08-05 23:58:29.567 | INFO     | src.run.eval.retrieval:generate_synthetic_dataset:67 - Creating new synthetic retrieval eval dataset...
100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:21<00:00,  1.08s/it]
2024-08-05 23:58:51.231 | INFO     | src.run.eval.retrieval:generate_synthetic_dataset:74 - Persisting synthetic retrieval eval dataset to data/005_use_smaller_embedding_model/retrieval_synthetic_eval_dataset.json...


In [36]:
retrieval_evaluator.retrieval_eval_dataset.queries

{'c49cb0bf-3225-4936-98af-82f1cc697ea2': "LaFitte's New Orleans Creole Cookery reviews",
 '4c18d768-0b4d-40c6-b824-03cd73833448': 'received without damage review',
 'c93e5aef-2235-4811-b0aa-351dfa1c7af8': 'Nashville grocery store reviews',
 '332d4aa7-5245-4fcc-9bb1-55603ba3e018': 'poor experience',
 '2655c66b-d2e4-4765-83b1-d4ae9bf5087e': 'ice cream flavors review',
 '6ffa4e63-1a49-426b-b308-7d81563d5d04': 'ice cream waffle cones Nashville',
 '0d1c1ce2-baa7-4e9a-b0d6-5af846a4c584': "Tuna Bar Valentine's Day reservation reviews",
 '098afe3f-8993-4621-acd8-67d04fc8a845': 'coffee and breakfast sandwich reviews',
 '801243d2-850d-4809-b293-32b640ff006e': 'Chase credit card complaints',
 '29c39d17-ae54-4fc6-8675-358e4cefa459': "Tony's Alton restaurant experience review",
 '87da9f76-2b29-46b3-b7c8-38d85c34e6be': 'Bala Better Health Lipo Laser Radio Frequency reviews',
 'b75fd256-8cf4-40f9-912a-317932cd6d95': 'CMA Fest ice cream flavors',
 '2682ed32-a9e0-4444-8920-b1dc9435fe6d': 'shopping with

In [37]:
retrieval_eval_results_df, retrieval_eval_results_full_df = await retrieval_evaluator.aevaluate(cfg, retriever)

> Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.564439] Would try it again.
> [Node 356b006b-7072-4232-b577-c9893412906f] [Similarity score:             0.562288] So I paid for items not provided :/. Lesson learned. Sorry I absolutely do not recommend the place.
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.557303] I can't recommend it highly enough
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.555047] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.553888] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8] [Similarity score:             0.553148] Will definitely order from here again!
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.552123] We did not complain or say another word. We just packed up and left
> [Node 634d55c

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.564439] Would try it again.
> [Node 356b006b-7072-4232-b577-c9893412906f] [Similarity score:             0.562288] So I paid for items not provided :/. Lesson learned. Sorry I absolutely do not recommend the place.
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.557303] I can't recommend it highly enough
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.555047] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.553888] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8] [Similarity score:             0.553148] Will definitely order from here again!
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.552123] We did not complain or say another word. We 

> Top 10 nodes:
> [Node b494136e-9882-4bcc-bcfc-8cafe48ad168] [Similarity score:             0.580504] And not an understatement the food was amazing definitely worth checking out
> [Node 3a79ef56-24b2-457b-ab5b-cd30fc588d7c] [Similarity score:             0.580226] was visiting NOLA in 2016, and by chance I ended up here for lunch.  I don't know about the other...
> [Node 4ba8d740-d949-41fd-8c5b-7cf5e02a3f5e] [Similarity score:             0.572968] For the most part it was good. My party had for appetizers the onion straws- really onion rings, ...
> [Node 15127e78-a18b-4917-8def-26cbab2c6cc5] [Similarity score:             0.572007] Thanks for a wonderful fun filled evening!
> [Node b7c54980-2064-4717-a208-d9e1a61a4f38] [Similarity score:             0.571981] My siblings and I came in last night for dinner for the first time. The server was great she was ...
> [Node e6c8130b-8e39-45e1-9d03-b75c40f104ae] [Similarity score:             0.571061] Decided to give the new restaurant a tr

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node b494136e-9882-4bcc-bcfc-8cafe48ad168] [Similarity score:             0.580504] And not an understatement the food was amazing definitely worth checking out
> [Node 3a79ef56-24b2-457b-ab5b-cd30fc588d7c] [Similarity score:             0.580226] was visiting NOLA in 2016, and by chance I ended up here for lunch.  I don't know about the other...
> [Node 4ba8d740-d949-41fd-8c5b-7cf5e02a3f5e] [Similarity score:             0.572968] For the most part it was good. My party had for appetizers the onion straws- really onion rings, ...
> [Node 15127e78-a18b-4917-8def-26cbab2c6cc5] [Similarity score:             0.572007] Thanks for a wonderful fun filled evening!
> [Node b7c54980-2064-4717-a208-d9e1a61a4f38] [Similarity score:             0.571981] My siblings and I came in last night for dinner for the first time. The server was great she was ...
> [Node e6c8130b-8e39-45e1-9d03-b75c40f104ae] [Similarity score:             0.571061] 

> Top 10 nodes:
> [Node b975f0a1-2a35-4dc1-8315-cd414ebf0015] [Similarity score:             0.617034] Love this place
> [Node 11181be4-353e-4f2d-a4bb-7c7dd05fa3e8] [Similarity score:             0.614194] Will definitely order from here again!
> [Node e387605a-a115-4f90-9d1d-ea4a76b9e0a8] [Similarity score:             0.604378] Dont expect anything fancy. My boyfriend and I order take out there and the manager is always so ...
> [Node bf0d0553-8994-40e7-af47-b3f8d2c3559c] [Similarity score:             0.601715] I would recommend this place!
> [Node 5939d19d-6ca9-4b60-9b62-aef109eaff80] [Similarity score:             0.592903] You see what you and order and it comes out right away.
Love it will be back later in the week
> [Node c1dfb2ad-0142-45ba-a97a-0c8d317862df] [Similarity score:             0.590777] I think they're going out of business! 
> [Node d0d52dcc-d0d6-4938-9c82-bf5103d42af9] [Similarity score:             0.58822] I tried this restaurant because of the Yelp reviews.  T

...

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node b5f52489-30ee-42df-a290-3b6e1d92c68d] [Similarity score:             0.591743] There were long lines for food and check out at lunchtime on a Sunday. Only 1 cashier was working...
> [Node 044b6706-39a1-41d7-8278-379941271897] [Similarity score:             0.587063] Got try it
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.581776] We did not complain or say another word. We just packed up and left
> [Node c8941651-9e63-4423-a06c-e9f91071d63d] [Similarity score:             0.580716] Food was on point and drinks were delicious too
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.57808] !! I might stalk them now
> [Node 7bec354e-f9e4-49e2-8f18-62b7fbfcf3f2] [Similarity score:             0.576954] I would highly recommend stopping by if you ever see them out and about or need a lunch option fo...
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:     

> Top 10 nodes:
> [Node 044b6706-39a1-41d7-8278-379941271897] [Similarity score:             0.632765] Got try it
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.62919] We did not complain or say another word. We just packed up and left
> [Node c8941651-9e63-4423-a06c-e9f91071d63d] [Similarity score:             0.625877] Food was on point and drinks were delicious too
> [Node 67bc3fb2-aaec-43bb-b542-98b0f142a25f] [Similarity score:             0.608958] I will be back!
> [Node 12772529-5860-4d9f-b33f-e346fccebdc8] [Similarity score:             0.607188] I love this bar!  I've been here twice, not during peak bar hours so I'm sure it's even more fun ...
> [Node 414deb3c-08cf-4715-8112-a56d0d060f7e] [Similarity score:             0.597805] Yeah I will be back.
> [Node 650b3a9c-3c5c-4bf4-9eeb-3a001ef82e35] [Similarity score:             0.588265] This was my first and definitely last time. I would not recommend. I was being generous to give i...
> [Node 57

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 044b6706-39a1-41d7-8278-379941271897] [Similarity score:             0.632765] Got try it
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.62919] We did not complain or say another word. We just packed up and left
> [Node c8941651-9e63-4423-a06c-e9f91071d63d] [Similarity score:             0.625877] Food was on point and drinks were delicious too
> [Node 67bc3fb2-aaec-43bb-b542-98b0f142a25f] [Similarity score:             0.608958] I will be back!
> [Node 12772529-5860-4d9f-b33f-e346fccebdc8] [Similarity score:             0.607188] I love this bar!  I've been here twice, not during peak bar hours so I'm sure it's even more fun ...
> [Node 414deb3c-08cf-4715-8112-a56d0d060f7e] [Similarity score:             0.597805] Yeah I will be back.
> [Node 650b3a9c-3c5c-4bf4-9eeb-3a001ef82e35] [Similarity score:             0.588265] This was my first and definitely last time. I would not recommend. I was

> Top 10 nodes:
> [Node cc385d5b-bcb0-411e-921b-63597fb7931b] [Similarity score:             0.604959] The food was amazing, our server was kind and pleasant, and the owner came over to check in on us...
> [Node 7bec354e-f9e4-49e2-8f18-62b7fbfcf3f2] [Similarity score:             0.601298] I would highly recommend stopping by if you ever see them out and about or need a lunch option fo...
> [Node a5cf542f-1062-4bc2-b1c7-8cf45b5e9c16] [Similarity score:             0.596321] Just had my wedding on 7/22/2017 and Rob was amazing:) he felt part of the family/friends of my i...
> [Node a9a9a3f3-b379-4aa2-9a51-9eac208eee4e] [Similarity score:             0.59412] We are very pleased with our choice for our wedding DJ. Rob was very professional and attentive t...
> [Node 95f920dd-9fc8-4a39-b5ad-d925a8a1144d] [Similarity score:             0.591144] We still have wedding guests contacting us and telling us how fun everything was.
We couldn't rec...
> [Node 2e868a94-7309-4d70-8318-ffe7c7ad3117]

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node cc385d5b-bcb0-411e-921b-63597fb7931b] [Similarity score:             0.604959] The food was amazing, our server was kind and pleasant, and the owner came over to check in on us...
> [Node 7bec354e-f9e4-49e2-8f18-62b7fbfcf3f2] [Similarity score:             0.601298] I would highly recommend stopping by if you ever see them out and about or need a lunch option fo...
> [Node a5cf542f-1062-4bc2-b1c7-8cf45b5e9c16] [Similarity score:             0.596321] Just had my wedding on 7/22/2017 and Rob was amazing:) he felt part of the family/friends of my i...
> [Node a9a9a3f3-b379-4aa2-9a51-9eac208eee4e] [Similarity score:             0.59412] We are very pleased with our choice for our wedding DJ. Rob was very professional and attentive t...
> [Node 95f920dd-9fc8-4a39-b5ad-d925a8a1144d] [Similarity score:             0.591144] We still have wedding guests contacting us and telling us how fun everything was.
We couldn't rec...
> [Nod

In [38]:
retrieval_eval_results_df

retrievers  hit_rate    mrr  precision  recall     ap      ndcg
0  top_10_retrieval_eval       0.2  0.135       0.02     0.2  0.135  0.033209

In [40]:
retrieval_eval_results_full_df

query  \
0        LaFitte's New Orleans Creole Cookery reviews   
1                      received without damage review   
2                     Nashville grocery store reviews   
3                                     poor experience   
4                            ice cream flavors review   
5                    ice cream waffle cones Nashville   
6        Tuna Bar Valentine's Day reservation reviews   
7               coffee and breakfast sandwich reviews   
8                        Chase credit card complaints   
9           Tony's Alton restaurant experience review   
10  Bala Better Health Lipo Laser Radio Frequency ...   
11                         CMA Fest ice cream flavors   
12                   shopping with a friend June 2019   
13                    Caviar & Bananas breakfast menu   
14                                      gifts for men   
15             delicious cocktails and wine selection   
16                          coffee and treats reviews   
17                             What did my son enjoy?   
18            family wedding dinner Ricardo's reviews   
19                  great drinks happy hour cocktails   

                              expected_ids  \
0   [a0725bda-b426-4e7e-8757-ad47bb224c3d]   
1   [e2cbc17a-773c-49bd-9430-d66e5554e3e8]   
2   [f8ed749d-5b97-4a1a-a61a-4188242ad928]   
3   [730ff7c8-741e-4983-a359-5e7f93548501]   
4   [996c0ebb-3af2-444a-8eba-d4d2b17c2caa]   
5   [a152030d-54ed-48e2-b6ef-52d2bb6ef8c2]   
6   [5fb29114-756d-445c-9ab5-8ddffedd2018]   
7   [afc3a1b4-2892-43f8-b6ae-b857636f1486]   
8   [567ae8af-966b-482b-9189-73935a365e4d]   
9   [44c12937-f4c9-4bcb-a223-9436e2740669]   
10  [34608595-a7fa-4c23-9588-991d39f5cd68]   
11  [87e53bdd-71aa-426c-87a6-8c31f3f9134a]   
12  [da802b31-6ea9-4312-8514-298321f7efc2]   
13  [b5161b97-5a09-4823-b8ef-ea347e3348de]   
14  [8d977ad0-5575-4640-9b16-92797aa0c430]   
15  [8347e41d-9d96-45a1-b23e-31eacfd13dd8]   
16  [809102e9-9e7f-4321-b767-b63f5fbb2b9a]   
17  [0731c00d-5bae-428d-94ad-91a0755d62da]   
18  [819dfb2a-bc70-4364-8270-91c5760b0a3d]   
19  [19c55202-dd8e-4095-afc2-3e32dcd91153]   

                                      retrieved_texts  hit_rate  mrr  \
0   [And not an understatement the food was amazin...       0.0  0.0   
1   [Would try it again., So I paid for items not ...       0.0  0.0   
2   [Love this place, Will definitely order from h...       0.0  0.0   
3   [So I paid for items not provided :/. Lesson l...       0.0  0.0   
4   [!! I might stalk them now, Got try it, I woul...       0.0  0.0   
5   [My husband and I came here to take a break fr...       0.0  0.0   
6   [Food was not that great. I ordered 2 differen...       0.0  0.0   
7   [There were long lines for food and check out ...       0.0  0.0   
8   [Every person I have spoken with has a differe...       1.0  0.2   
9   [So....I want to be fair to Tony's but I also ...       1.0  0.5   
10  [Bala Better Health is extremely professional ...       1.0  1.0   
11  [I stopped in during CMA Fest in the afternoon...       1.0  1.0   
12  [Will definitely order from here again!, I wou...       0.0  0.0   
13  [The decor is beautiful and I could spend hour...       0.0  0.0   
14  [Definitely try this place for yourself, More ...       0.0  0.0   
15  [Got try it, Food was on point and drinks were...       0.0  0.0   
16  [There were long lines for food and check out ...       0.0  0.0   
17  [Definitely try this place for yourself, Didn'...       0.0  0.0   
18  [The food was amazing, our server was kind and...       0.0  0.0   
19  [Got try it, We did not complain or say anothe...       0.0  0.0   

    precision  recall   ap      ndcg  
0         0.0     0.0  0.0  0.000000  
1         0.0     0.0  0.0  0.000000  
2         0.0     0.0  0.0  0.000000  
3         0.0     0.0  0.0  0.000000  
4         0.0     0.0  0.0  0.000000  
5         0.0     0.0  0.0  0.000000  
6         0.0     0.0  0.0  0.000000  
7         0.0     0.0  0.0  0.000000  
8         0.1     1

#### Error Analysis

In [41]:
retrieval_eval_irrelevance_df = (
    retrieval_eval_results_full_df
    .loc[lambda df: df['hit_rate'].lt(1)]
    .sort_values(['hit_rate', 'mrr', 'precision', 'recall', 'ap', 'ndcg'])
)
retrieval_eval_irrelevance_df

query  \
0   LaFitte's New Orleans Creole Cookery reviews   
1                 received without damage review   
2                Nashville grocery store reviews   
3                                poor experience   
4                       ice cream flavors review   
5               ice cream waffle cones Nashville   
6   Tuna Bar Valentine's Day reservation reviews   
7          coffee and breakfast sandwich reviews   
12              shopping with a friend June 2019   
13               Caviar & Bananas breakfast menu   
14                                 gifts for men   
15        delicious cocktails and wine selection   
16                     coffee and treats reviews   
17                        What did my son enjoy?   
18       family wedding dinner Ricardo's reviews   
19             great drinks happy hour cocktails   

                              expected_ids  \
0   [a0725bda-b426-4e7e-8757-ad47bb224c3d]   
1   [e2cbc17a-773c-49bd-9430-d66e5554e3e8]   
2   [f8ed749d-5b97-4a1a-a61a-4188242ad928]   
3   [730ff7c8-741e-4983-a359-5e7f93548501]   
4   [996c0ebb-3af2-444a-8eba-d4d2b17c2caa]   
5   [a152030d-54ed-48e2-b6ef-52d2bb6ef8c2]   
6   [5fb29114-756d-445c-9ab5-8ddffedd2018]   
7   [afc3a1b4-2892-43f8-b6ae-b857636f1486]   
12  [da802b31-6ea9-4312-8514-298321f7efc2]   
13  [b5161b97-5a09-4823-b8ef-ea347e3348de]   
14  [8d977ad0-5575-4640-9b16-92797aa0c430]   
15  [8347e41d-9d96-45a1-b23e-31eacfd13dd8]   
16  [809102e9-9e7f-4321-b767-b63f5fbb2b9a]   
17  [0731c00d-5bae-428d-94ad-91a0755d62da]   
18  [819dfb2a-bc70-4364-8270-91c5760b0a3d]   
19  [19c55202-dd8e-4095-afc2-3e32dcd91153]   

                                      retrieved_texts  hit_rate  mrr  \
0   [And not an understatement the food was amazin...       0.0  0.0   
1   [Would try it again., So I paid for items not ...       0.0  0.0   
2   [Love this place, Will definitely order from h...       0.0  0.0   
3   [So I paid for items not provided :/. Lesson l...       0.0  0.0   
4   [!! I might stalk them now, Got try it, I woul...       0.0  0.0   
5   [My husband and I came here to take a break fr...       0.0  0.0   
6   [Food was not that great. I ordered 2 differen...       0.0  0.0   
7   [There were long lines for food and check out ...       0.0  0.0   
12  [Will definitely order from here again!, I wou...       0.0  0.0   
13  [The decor is beautiful and I could spend hour...       0.0  0.0   
14  [Definitely try this place for yourself, More ...       0.0  0.0   
15  [Got try it, Food was on point and drinks were...       0.0  0.0   
16  [There were long lines for food and check out ...       0.0  0.0   
17  [Definitely try this place for yourself, Didn'...       0.0  0.0   
18  [The food was amazing, our server was kind and...       0.0  0.0   
19  [Got try it, We did not complain or say anothe...       0.0  0.0   

    precision  recall   ap  ndcg  
0         0.0     0.0  0.0   0.0  
1         0.0     0.0  0.0   0.0  
2         0.0     0.0  0.0   0.0  
3         0.0     0.0  0.0   0.0  
4         0.0     0.0  0.0   0.0  
5         0.0     0.0  0.0   0.0  
6         0.0     0.0  0.0   0.0  
7         0.0     0.0  0.0   0.0  
12        0.0     0.0  0.0   0.0  
13        0.0     0.0  0.0   0.0  
14        0.0     0.0  0.0   0.0  
15        0.0     0.0  0.0   0.0  
16        0.0     0.0  0.0   0.0  
17        0.0     0.0  0.0   0.0  
18        0.0     0.0  0.0   0.0  
19        0.0     0.0  0.0   0.0

In [42]:
for i, row in retrieval_eval_irrelevance_df.reset_index(drop=True).iterrows():
    print(f"\n\n============Error #{i+1}=============\n\n")
    print(f"Query:\n{row.query}\n")
    expected_contexts = [json.loads(record.payload['_node_content'])['text'] for record in qdrantdb.retrieve(cfg.db_collection, ids=row.expected_ids)]
    expected_contexts = '\n\n'.join(expected_contexts)
    print(f"Expected Contexts:\n{expected_contexts}\n")
    contexts = ""
    for i, context in enumerate(row.retrieved_texts):
        contexts = f"{contexts}\n\nContext #{i+1}: {context}"
    print(f"Retrieved Contexts:\n{contexts}\n")



============Error #1=============


Query:
LaFitte's New Orleans Creole Cookery reviews

Expected Contexts:
LaFitte's is a new venture of A J Tusa, owner of New Orleans  Creole Cookery.

Large parking lot just off LAPLCO Blvd & Manhattan.



Retrieved Contexts:


Context #1: And not an understatement the food was amazing definitely worth checking out

Context #2: was visiting NOLA in 2016, and by chance I ended up here for lunch.  I don't know about the other reviews... I had great food and service.  

Context #3: For the most part it was good. My party had for appetizers the onion straws- really onion rings, very good but expected thinner cut due to name; the seafood queso-very good; the gumbo was reported as good ( I didn't eat any);  the fried soft shell crab plate- very good, nice size but way too many fries, should have been served on toast as most places do to for oil draining which flavors the toast; an oyster poboy and a shrimp poboy were over loaded with fresh fried seafood 

# Response

In [43]:
from llama_index.core import get_response_synthesizer
from llama_index.core.postprocessor import SimilarityPostprocessor
from llama_index.postprocessor.flag_embedding_reranker import FlagEmbeddingReranker

from src.features.append_reference.custom_query_engine import ManualAppendReferenceQueryEngine

In [44]:
node_postprocessors = []

if cfg.retrieval_cfg.retrieval_similarity_cutoff is not None:
    node_postprocessors.append(SimilarityPostprocessor(similarity_cutoff=cfg.retrieval_cfg.retrieval_similarity_cutoff))

reranker = FlagEmbeddingReranker(model=cfg.retrieval_cfg.rerank_model_name, top_n=cfg.retrieval_cfg.rerank_top_k)
node_postprocessors.append(reranker)

response_synthesizer = get_response_synthesizer()
query_engine = ManualAppendReferenceQueryEngine(
    retriever=retriever,
    response_synthesizer=response_synthesizer,
    node_postprocessors=node_postprocessors,
)

## Test Query Engine

In [45]:
from llama_index.core.response.notebook_utils import (
    display_source_node,
    display_response,
)

In [47]:
question = "nearby Santa Barbara"
response = query_engine.query(question)
display_response(response, show_source=True, show_metadata=True, show_source_metadata=True)

> Top 10 nodes:
> [Node bf0d0553-8994-40e7-af47-b3f8d2c3559c] [Similarity score:             0.611767] I would recommend this place!
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.605758] Would try it again.
> [Node fbffef3e-d626-4160-b519-487eef8dfaeb] [Similarity score:             0.602596] Wish I would have gotten some
> [Node e1abcd6d-c15f-478c-953e-dfe0fec87dd0] [Similarity score:             0.601938] I will definitely be back soon!
> [Node 457ebb32-30dd-4040-96fd-e4be99b092b4] [Similarity score:             0.600253] Will be back first chance we get!
> [Node b949e08a-d9e4-4d7f-920b-fc54e28899b0] [Similarity score:             0.599474] Order was delayed and no communication with cashier and kitchen
> [Node d9213cd2-1b51-478d-ab29-8d30d1001b40] [Similarity score:             0.59893] I'll be back again for sure!!!
> [Node 8ed26e8f-c3bb-454b-8b4f-14190fbe7e71] [Similarity score:             0.598665] We both got
> [Node 1aaa8e70-05c9-48f6-83e5-44ad

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node bf0d0553-8994-40e7-af47-b3f8d2c3559c] [Similarity score:             0.611767] I would recommend this place!
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.605758] Would try it again.
> [Node fbffef3e-d626-4160-b519-487eef8dfaeb] [Similarity score:             0.602596] Wish I would have gotten some
> [Node e1abcd6d-c15f-478c-953e-dfe0fec87dd0] [Similarity score:             0.601938] I will definitely be back soon!
> [Node 457ebb32-30dd-4040-96fd-e4be99b092b4] [Similarity score:             0.600253] Will be back first chance we get!
> [Node b949e08a-d9e4-4d7f-920b-fc54e28899b0] [Similarity score:             0.599474] Order was delayed and no communication with cashier and kitchen
> [Node d9213cd2-1b51-478d-ab29-8d30d1001b40] [Similarity score:             0.59893] I'll be back again for sure!!!
> [Node 8ed26e8f-c3bb-454b-8b4f-14190fbe7e71] [Similarity score:             0.598665] We both g

**`Final Response:`** It seems that there are several bakeries and restaurants in the area that are worth visiting. If you're looking for a place to grab a bite to eat in Santa Barbara, you might want to consider checking out some of the local eateries.


Sources:
- [None](None)

---

**`Source Node 1/5`**

...

**Node ID:** b949e08a-d9e4-4d7f-920b-fc54e28899b0<br>**Similarity:** -4.084694862365723<br>**Text:** Order was delayed and no communication with cashier and kitchen<br>**Metadata:** {'review_id': 'T9L6Fbhzv7662VLSvtJpVA', 'user_id': 'xbBGgu9CJq5l9IyG9mCE9Q', 'business_id': 'IDtLPgUrqorrpqSLdfMhZQ', 'review_stars': 1, 'useful': 1, 'funny': 0, 'cool': 0, 'date': '2017-12-30T20:13:44', 'biz_name': 'Helena Avenue Bakery', 'biz_address': '131 Anacapa St, Ste C', 'biz_city': 'Santa Barbara', 'biz_state': 'CA', 'biz_postal_code': '93101', 'biz_latitude': 34.4144445, 'biz_longitude': -119.6906718, 'biz_stars': 4.0, 'biz_review_count': 389, 'biz_is_open': 1, 'biz_attributes': {'AcceptsInsurance': None, 'Alcohol': "u'none'", 'Ambience': "{'touristy': False, 'hipster': True, 'romantic': False, 'divey': False, 'intimate': False, 'trendy': True, 'upscale': False, 'classy': False, 'casual': True}", 'BYOB': None, 'BestNights': None, 'BikeParking': 'True', 'BusinessAcceptsBitcoin': None, 'BusinessAcceptsCreditCards': 'True', 'BusinessParking': "{'garage': False, 'street': True, 'validated': False, 'lot': False, 'valet': False}", 'ByAppointmentOnly': None, 'Caters': 'True', 'CoatCheck': None, 'Corkage': None, 'DogsAllowed': 'True', 'DriveThru': None, 'GoodForDancing': None, 'GoodForKids': 'True', 'GoodForMeal': "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': False, 'brunch': True, 'breakfast': True}", 'HappyHour': 'False', 'HasTV': 'False', 'Music': None, 'NoiseLevel': "u'average'", 'OutdoorSeating': 'True', 'RestaurantsAttire': "'casual'", 'RestaurantsDelivery': 'None', 'RestaurantsGoodForGroups': 'True', 'RestaurantsPriceRange2': '2', 'RestaurantsReservations': 'False', 'RestaurantsTableService': 'False', 'RestaurantsTakeOut': 'True', 'Smoking': None, 'WheelchairAccessible': 'True', 'WiFi': "u'no'"}, 'biz_categories': ['Food', 'Restaurants', 'Salad', 'Coffee & Tea', 'Breakfast & Brunch', 'Sandwiches', 'Bakeries'], 'biz_hours': {'Friday': '8:0-14:0', 'Monday': '0:0-0:0', 'Saturday': '8:0-14:0', 'Sunday': '8:0-14:0', 'Thursday': '8:0-14:0', 'Tuesday': '8:0-14:0', 'Wednesday': '8:0-14:0'}}<br>

---

**`Source Node 5/5`**

**Node ID:** bf0d0553-8994-40e7-af47-b3f8d2c3559c<br>**Similarity:** -7.764894008636475<br>**Text:** I would recommend this place!<br>**Metadata:** {'review_id': '4Jri4fP-ddh2GJ8aLfCUZA', 'user_id': 'JKvGx3YKsSFc5qV4lh9CGQ', 'business_id': 'ROeacJQwBeh05Rqg7F6TCg', 'review_stars': 4, 'useful': 0, 'funny': 0, 'cool': 0, 'date': '2017-06-15T23:20:28', 'biz_name': 'BAP', 'biz_address': '1224 South St', 'biz_city': 'Philadelphia', 'biz_state': 'PA', 'biz_postal_code': '19147', 'biz_latitude': 39.943223, 'biz_longitude': -75.162568, 'biz_stars': 4.5, 'biz_review_count': 205, 'biz_is_open': 1, 'biz_attributes': {'AcceptsInsurance': None, 'Alcohol': "u'none'", 'Ambience': "{'touristy': False, 'hipster': False, 'romantic': False, 'divey': False, 'intimate': None, 'trendy': False, 'upscale': False, 'classy': False, 'casual': True}", 'BYOB': None, 'BestNights': None, 'BikeParking': 'True', 'BusinessAcceptsBitcoin': None, 'BusinessAcceptsCreditCards': 'True', 'BusinessParking': "{'garage': False, 'street': True, 'validated': False, 'lot': False, 'valet': False}", 'ByAppointmentOnly': None, 'Caters': 'True', 'CoatCheck': None, 'Corkage': None, 'DogsAllowed': None, 'DriveThru': None, 'GoodForDancing': None, 'GoodForKids': 'True', 'GoodForMeal': "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': True, 'brunch': False, 'breakfast': False}", 'HappyHour': None, 'HasTV': 'True', 'Music': None, 'NoiseLevel': "u'quiet'", 'OutdoorSeating': 'None', 'RestaurantsAttire': "u'casual'", 'RestaurantsDelivery': 'None', 'RestaurantsGoodForGroups': 'False', 'RestaurantsPriceRange2': '1', 'RestaurantsReservations': 'False', 'RestaurantsTableService': 'True', 'RestaurantsTakeOut': 'True', 'Smoking': None, 'WheelchairAccessible': None, 'WiFi': "u'no'"}, 'biz_categories': ['Korean', 'Restaurants'], 'biz_hours': {'Friday': '11:30-20:30', 'Monday': '11:30-20:30', 'Saturday': '11:30-20:30', 'Sunday': None, 'Thursday': '11:30-20:30', 'Tuesday': '11:30-20:30', 'Wednesday': '11:30-20:30'}}<br>

{'8ed26e8f-c3bb-454b-8b4f-14190fbe7e71': {'review_id': 'UABngZyZKqDff2Gjx6O3mw',
  'user_id': 'U-blmCm_qUbibUUgqDSB_g',
  'business_id': 'IDtLPgUrqorrpqSLdfMhZQ',
  'review_stars': 4,
  'useful': 6,
  'funny': 4,
  'cool': 7,
  'date': '2018-10-29T15:28:05',
  'biz_name': 'Helena Avenue Bakery',
  'biz_address': '131 Anacapa St, Ste C',
  'biz_city': 'Santa Barbara',
  'biz_state': 'CA',
  'biz_postal_code': '93101',
  'biz_latitude': 34.4144445,
  'biz_longitude': -119.6906718,
  'biz_stars': 4.0,
  'biz_review_count': 389,
  'biz_is_open': 1,
  'biz_attributes': {'AcceptsInsurance': None,
   'Alcohol': "u'none'",
   'Ambience': "{'touristy': False, 'hipster': True, 'romantic': False, 'divey': False, 'intimate': False, 'trendy': True, 'upscale': False, 'classy': False, 'casual': True}",
   'BYOB': None,
   'BestNights': None,
   'BikeParking': 'True',
   'BusinessAcceptsBitcoin': None,
   'BusinessAcceptsCreditCards': 'True',
   'BusinessParking': "{'garage': False, 'street': True, 'v

## Response Evaluation

In [48]:
from src.run.eval import ResponseEvaluator

In [49]:
response_evaluator = ResponseEvaluator()

### Synthetic

In [50]:
response_eval_documents, response_synthetic_eval_dataset = response_evaluator.generate_synthetic_dataset(cfg, documents)

2024-08-06 00:04:34.103 | INFO     | src.run.eval.response:generate_synthetic_dataset:39 - Sampling 10 documents for response evaluation...
2024-08-06 00:04:34.110 | INFO     | src.run.eval.response:generate_synthetic_dataset:59 - Creating new response eval dataset at data/005_use_smaller_embedding_model/response_synthetic_eval_dataset.json...
2024-08-06 00:04:34.111 | INFO     | src.run.eval.response:generate_synthetic_dataset:62 - Creating synthetic response eval dataset...


Parsing nodes:   0%|          | 0/10 [00:00<?, ?it/s]

> Adding chunk: Exceeded my expectations. Bring a small group s...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: Exceeded my expectations. Bring a small group s...


> Adding chunk: I had the worst customer service of my life. Th...


...

DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: They renovated the space well. The lighting & a...


> Adding chunk: I love this place for the atmosphere and the am...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I love this place for the atmosphere and the am...


> Adding chunk: Before I start with the compliments, I have to ...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: Before I start with the compliments, I have to ...
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:02<00:00,  2.08s/it]
2024-08-06 00:04:58.519 | INFO     | src.run.eval.response:generate_synthetic_dataset:85 - Persisting synthetic response eval dataset at data/005_use_smaller_embedding_model/response_synthetic_eval_dataset.json...


In [51]:
response_synthetic_eval_prediction_dataset = await response_synthetic_eval_dataset.amake_predictions_with(
    predictor=query_engine, batch_size=cfg.batch_size, show_progress=True
)

Batch processing of predictions:   0%|                                                                                                                                                                        | 0/10 [00:00<?, ?it/s]

> Top 10 nodes:
> [Node cb3a5073-a719-4fb6-8996-da8cf7f8e37a] [Similarity score:             0.629423] The drink is the only reason I would give this review 4 stars because it was watered down. The wa...
> [Node d409e191-5090-4daa-bba2-c37af9ed1c3e] [Similarity score:             0.626662] The staff is all very nice - my waiter recommended this cocktail and I wasn't disappointed; howev...
> [Node b494136e-9882-4bcc-bcfc-8cafe48ad168] [Similarity score:             0.608501] And not an understatement the food was amazing definitely worth checking out
> [Node 5c43400b-236c-4a02-ab6e-ce0019880806] [Similarity score:             0.608068] I don't have anything bad to say! Our server, Justin, was very informative and so much fun! I can...
> [Node 302964ab-7e28-488a-bac1-9a3f16f4fe1b] [Similarity score:             0.607732] I went here for the first time a couple weeks ago! I loved it so much that I would definitely go ...
> [Node cc81ab53-c21c-4983-86e5-e6b7b2539741] [Similarity score:    

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node cb3a5073-a719-4fb6-8996-da8cf7f8e37a] [Similarity score:             0.629423] The drink is the only reason I would give this review 4 stars because it was watered down. The wa...
> [Node d409e191-5090-4daa-bba2-c37af9ed1c3e] [Similarity score:             0.626662] The staff is all very nice - my waiter recommended this cocktail and I wasn't disappointed; howev...
> [Node b494136e-9882-4bcc-bcfc-8cafe48ad168] [Similarity score:             0.608501] And not an understatement the food was amazing definitely worth checking out
> [Node 5c43400b-236c-4a02-ab6e-ce0019880806] [Similarity score:             0.608068] I don't have anything bad to say! Our server, Justin, was very informative and so much fun! I can...
> [Node 302964ab-7e28-488a-bac1-9a3f16f4fe1b] [Similarity score:             0.607732] I went here for the first time a couple weeks ago! I loved it so much that I would definitely go ...
> [Node cc81ab53-c21c-4983-86

> Top 10 nodes:
> [Node af0c6c2b-b9d1-41c6-810c-9400c9d0e32d] [Similarity score:             0.654603] The manager Paul on the other hand was rude and disrespectful to myself my friends and other gues...
> [Node 5af3b74e-43a8-4cc4-8b60-fbe3977fae46] [Similarity score:             0.641234] She truly cared about our table . Ask for her!
Paul the manager was great
> [Node d5aae5a6-9d57-4004-8240-d31da9e2a3b1] [Similarity score:             0.639946] He very rudely said "no" to which I asked what the difference was between his cloth scarf and my ...
> [Node aace97b5-324f-4816-9dcc-f2ed926333af] [Similarity score:             0.639413] We were very disappointed. Our server was clueless, rude and lazy. She was much more interested i...
> [Node cebad052-fdaf-4bf8-bfbc-cb0c7fc370c9] [Similarity score:             0.629484] I had a phenomenal experience at twin peaks this evening. Our server, shayla, was a lot of fun an...
> [Node f04ff36e-0502-4d6a-a020-c7890e0c9eaf] [Similarity score:       

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node af0c6c2b-b9d1-41c6-810c-9400c9d0e32d] [Similarity score:             0.654603] The manager Paul on the other hand was rude and disrespectful to myself my friends and other gues...
> [Node 5af3b74e-43a8-4cc4-8b60-fbe3977fae46] [Similarity score:             0.641234] She truly cared about our table . Ask for her!
Paul the manager was great
> [Node d5aae5a6-9d57-4004-8240-d31da9e2a3b1] [Similarity score:             0.639946] He very rudely said "no" to which I asked what the difference was between his cloth scarf and my ...
> [Node aace97b5-324f-4816-9dcc-f2ed926333af] [Similarity score:             0.639413] We were very disappointed. Our server was clueless, rude and lazy. She was much more interested i...
> [Node cebad052-fdaf-4bf8-bfbc-cb0c7fc370c9] [Similarity score:             0.629484] I had a phenomenal experience at twin peaks this evening. Our server, shayla, was a lot of fun an...
> [Node f04ff36e-0502-4d6a-a020-

...

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 90d413e5-eb5c-42d1-814a-75f31058d27e] [Similarity score:             0.645852] Flavorful food paired with good service
> [Node c09feac5-1562-4325-b8a3-f4b390106a86] [Similarity score:             0.645007] Highly recommend
> [Node 9280effd-4b3e-4899-882f-c37e0f2cc905] [Similarity score:             0.636359] I literally came here twice in one week because I wanted to try more things on the menu. Everythi...
> [Node fd8f8b52-04df-4073-8046-35618be2cadd] [Similarity score:             0.63073] We'll be back!
> [Node 2d7e83dc-fe63-4830-8fd1-d3bfdd08be8d] [Similarity score:             0.629943] Service was excellent!! 

Looking forward to many more visits
> [Node e7b0f18a-7178-4f72-aad2-4f073ffc6e85] [Similarity score:             0.623923] Absolutely incredible!!!!!!!!! We tried one of everything on the menu and not a single thing disa...
> [Node df30d0ab-ddfe-4dc2-aece-638f7551f887] [Similarity score:             0.617082] W

> Top 10 nodes:
> [Node 1a388bfc-b9c9-44a3-8e6b-e24660e13cb0] [Similarity score:             0.629102] Will be back for sure
> [Node 7111a1d6-6d1e-4c84-9c6d-f6e6846bd330] [Similarity score:             0.627068] First time and the last
> [Node 7cc08969-091e-4f9e-a999-3b06fa0b7f73] [Similarity score:             0.618858] Never again
> [Node 833855f2-8bc2-4a02-a799-2f5b5669e142] [Similarity score:             0.618235] Never had bad service or food!! Luv this place
> [Node 0bb5c8a5-e92c-4b79-85a4-57df0b796171] [Similarity score:             0.617117] Waited forever for food that was cold
> [Node 2e868a94-7309-4d70-8318-ffe7c7ad3117] [Similarity score:             0.6155] Would not recommend
> [Node 5f2cae3c-3a2f-49cd-a0d0-57f0e6e7097b] [Similarity score:             0.614541] THANKS EVERYONE!!!  Definitely will be back to try some other dishes -- YUMMO!!!

Eve & Paris
> [Node 063c4bde-faaf-4b2f-b714-69b20c134c62] [Similarity score:             0.61419] I thanked him again for making thi

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 1a388bfc-b9c9-44a3-8e6b-e24660e13cb0] [Similarity score:             0.629102] Will be back for sure
> [Node 7111a1d6-6d1e-4c84-9c6d-f6e6846bd330] [Similarity score:             0.627068] First time and the last
> [Node 7cc08969-091e-4f9e-a999-3b06fa0b7f73] [Similarity score:             0.618858] Never again
> [Node 833855f2-8bc2-4a02-a799-2f5b5669e142] [Similarity score:             0.618235] Never had bad service or food!! Luv this place
> [Node 0bb5c8a5-e92c-4b79-85a4-57df0b796171] [Similarity score:             0.617117] Waited forever for food that was cold
> [Node 2e868a94-7309-4d70-8318-ffe7c7ad3117] [Similarity score:             0.6155] Would not recommend
> [Node 5f2cae3c-3a2f-49cd-a0d0-57f0e6e7097b] [Similarity score:             0.614541] THANKS EVERYONE!!!  Definitely will be back to try some other dishes -- YUMMO!!!

Eve & Paris
> [Node 063c4bde-faaf-4b2f-b714-69b20c134c62] [Similarity score:             0.61

> Top 10 nodes:
> [Node 7787fbea-e88e-4f58-a58a-4f78d70bce97] [Similarity score:             0.644842] will definitely be back
> [Node abe0a622-bbec-4d94-8159-d764a5b7426e] [Similarity score:             0.631826] I want to try the salted latte's
> [Node 1375f3a6-13ed-4b84-a8f8-350128a748ec] [Similarity score:             0.614811] By far, my favourite coffeehouse in the city! I have never had great coffee until I started going...
> [Node c327c852-4a81-4aac-ad51-fcd33f25a354] [Similarity score:             0.611108] I really loved it here, makes me wish I lived closer and could stop by everyday! I had the dark h...
> [Node 8c4ee881-d2f0-454b-9e04-2ae674af69ce] [Similarity score:             0.604147] It looks fantastic, and I hope to have small work meetings here in the future!
> [Node 8d70cf23-99bf-43cd-bb53-59a37265f116] [Similarity score:             0.603612] I went there yesterday afternoon for the first time ever, and I feel like an idiot for not going ...
> [Node 7dcebcc6-1a47-4

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 7787fbea-e88e-4f58-a58a-4f78d70bce97] [Similarity score:             0.644842] will definitely be back
> [Node abe0a622-bbec-4d94-8159-d764a5b7426e] [Similarity score:             0.631826] I want to try the salted latte's
> [Node 1375f3a6-13ed-4b84-a8f8-350128a748ec] [Similarity score:             0.614811] By far, my favourite coffeehouse in the city! I have never had great coffee until I started going...
> [Node c327c852-4a81-4aac-ad51-fcd33f25a354] [Similarity score:             0.611108] I really loved it here, makes me wish I lived closer and could stop by everyday! I had the dark h...
> [Node 8c4ee881-d2f0-454b-9e04-2ae674af69ce] [Similarity score:             0.604147] It looks fantastic, and I hope to have small work meetings here in the future!
> [Node 8d70cf23-99bf-43cd-bb53-59a37265f116] [Similarity score:             0.603612] I went there yesterday afternoon for the first time ever, and I feel like an idiot fo

In [52]:
response_synthetic_mean_scores_df, response_synthetic_deep_eval_df = response_evaluator.evaluate_labelled_rag_dataset(
    response_synthetic_eval_dataset,
    response_synthetic_eval_prediction_dataset,
    dataset_name="synthetic",
    judge_model=cfg.eval_cfg.response_eval_llm_model,
    cache_dp=cfg.notebook_cache_dp
)

  0%|                                                                                                                                                                                                         | 0/10 [00:00<?, ?it/s]

> Adding chunk: Didnt love those.  Nice drinks and great asian ...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: Didnt love those.  Nice drinks and great asian ...


> Adding chunk: Absolutely incredible!!!!!!!!! We tried one of ...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: Absolutely incredible!!!!!!!!! We tried one of ...


...

DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I was very disappointed in this place. Dylan wa...


> Adding chunk: Came here on a Saturday night for our date nigh...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: Came here on a Saturday night for our date nigh...


> Adding chunk: (This was September 13, 2018. Hopefully, they'v...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: (This was September 13, 2018. Hopefully, they'v...
100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10/10 [01:07<00:00,  6.71s/it]


In [53]:
response_synthetic_mean_scores_df

rag                      base_rag
metrics                          
mean_correctness_score        2.2
mean_relevancy_score          0.7
mean_faithfulness_score       0.8

In [54]:
response_synthetic_deep_eval_df

query  \
0                  best dishes at The Green Pheasant   
1  plastic found in dessert at Romano's Macaroni ...   
2                  Copper Vine drink recommendations   
3  What did the reviewer think of the service at ...   
4                 chocolate chip cookie cones review   
5                       best coffeehouse in Edmonton   
6               Top Shelf Sports Lounge food quality   
7                   Bar One happy hour food specials   
8              Twin Peaks manager Paul rude behavior   
9                Copper Vine bathroom privacy issues   

                                              answer  relevancy_score  \
0  \nIt seems that the reviewers were thoroughly ...              1.0   
1  \nIt's not uncommon for restaurants to have oc...              0.0   
2  \n\nThe server at Copper Vine was able to reco...              1.0   
3  \n\nThe reviewer thought the service was poor,...              1.0   
4  \nThere is no mention of chocolate chip cookie...              0.0   
5  \n\nIt seems that one particular coffeehouse s...              1.0   
6  \n\nThe food is incredibly delicious, with man...              1.0   
7  \n\nDecent discounts on drinks, and a fairly v...              1.0   
8  \n\nIt's concerning to hear that some managers...              1.0   
9  \nIt's not uncommon for high-traffic establish...              0.0   

   correctness_score  faithfulness_score  \
0                2.0                 1.0   
1                2.0                 0.0   
2                3.0                 1.0   
3                1.0                 1.0   
4                1.0                 1.0   
5                3.0                 1.0   
6                4.0                 1.0   
7                2.0                 1.0   
8                2.0                 1.0   
9                2.0                 0.0   

                                            contexts  
0  [Didnt love those.  Nice drinks and great asia...  
1  [The prosciutto was hard and crunchy and barel...  
2  [She gave us the perfect recommendations and k...  
3  [My friend and I came here after waiting to tr...  
4  [You see what you and order and it comes out r...  
5  [By far, my favourite coffeehouse in the city!...  
6  [The service is phenomenal and attentive! Ever...  
7  [They renovated the space well. The lighting &...  
8  [The manager Paul on the other hand was rude a...  
9  [We ordered. Twenty minutes goes by (no food) ...

#### Error Analysis

In [55]:
response_synthetic_eval_dataset_dict = dict()
for example in response_synthetic_eval_dataset.examples:
    response_synthetic_eval_dataset_dict[example.query] = {
        "reference_answer": example.reference_answer,
        "reference_contexts": example.reference_contexts,
    }

In [56]:
response_synthetic_deep_eval_df.sort_values(['relevancy_score', 'correctness_score', 'faithfulness_score'])

query  \
4                 chocolate chip cookie cones review   
1  plastic found in dessert at Romano's Macaroni ...   
9                Copper Vine bathroom privacy issues   
3  What did the reviewer think of the service at ...   
0                  best dishes at The Green Pheasant   
7                   Bar One happy hour food specials   
8              Twin Peaks manager Paul rude behavior   
2                  Copper Vine drink recommendations   
5                       best coffeehouse in Edmonton   
6               Top Shelf Sports Lounge food quality   

                                              answer  relevancy_score  \
4  \nThere is no mention of chocolate chip cookie...              0.0   
1  \nIt's not uncommon for restaurants to have oc...              0.0   
9  \nIt's not uncommon for high-traffic establish...              0.0   
3  \n\nThe reviewer thought the service was poor,...              1.0   
0  \nIt seems that the reviewers were thoroughly ...              1.0   
7  \n\nDecent discounts on drinks, and a fairly v...              1.0   
8  \n\nIt's concerning to hear that some managers...              1.0   
2  \n\nThe server at Copper Vine was able to reco...              1.0   
5  \n\nIt seems that one particular coffeehouse s...              1.0   
6  \n\nThe food is incredibly delicious, with man...              1.0   

   correctness_score  faithfulness_score  \
4                1.0                 1.0   
1                2.0                 0.0   
9                2.0                 0.0   
3                1.0                 1.0   
0                2.0                 1.0   
7                2.0                 1.0   
8                2.0                 1.0   
2                3.0                 1.0   
5                3.0                 1.0   
6                4.0                 1.0   

                                            contexts  
4  [You see what you and order and it comes out r...  
1  [The prosciutto was hard and crunchy and barel...  
9  [We ordered. Twenty minutes goes by (no food) ...  
3  [My friend and I came here after waiting to tr...  
0  [Didnt love those.  Nice drinks and great asia...  
7  [They renovated the space well. The lighting &...  
8  [The manager Paul on the other hand was rude a...  
2  [She gave us the perfect recommendations and k...  
5  [By far, my favourite coffeehouse in the city!...  
6  [The service is phenomenal and attentive! Ever...

In [57]:
response_synthetic_eval_irrelevance_df = (
    response_synthetic_deep_eval_df
    .loc[lambda df: df['relevancy_score'].lt(1)]
    .sort_values(['relevancy_score', 'correctness_score', 'faithfulness_score'])
)

for i, row in response_synthetic_eval_irrelevance_df.reset_index(drop=True).iterrows():
    print(f"\n\n==============Error #{i+1}===============\n\n")
    print(f"Query:\n{row.query}\n")
    contexts = '\n\n'.join(row.contexts)
    print(f"Context:\n{contexts}\n")
    print(f"Answer:\n{row.answer}\n----\n")
    expected = response_synthetic_eval_dataset_dict.get(row.query)
    if not expected:
        logger.error(f"Could not find query {row.query} in synthetic_response_eval_dataset_dict!")
        continue
    expected_answer = expected['reference_answer']
    print(f"Expected Answer:\n{expected_answer}\n")
    expected_contexts = expected['reference_contexts']
    print(f"Expected Contexts:\n{expected_contexts}\n")



==============Error #1===============


Query:
chocolate chip cookie cones review

Context:
You see what you and order and it comes out right away.
Love it will be back later in the week

Food: 2-3 stars
Ambiance: 4 stars
Service: 3 stars
Price: 3 stars

I tried this restaurant because of the Yelp reviews.  The manager/Owner was quite pleasant.  Unfortunately, the food wasn't.  

Dont expect anything fancy. My boyfriend and I order take out there and the manager is always so friendly. I highly recommend this place!

I'll be back again for sure!!!

Answer:

There is no mention of chocolate chip cookie cones in the provided context information.


Sources:
- [None](None)



----

Expected Answer:
The chocolate chip cookie cones at Mike's Ice Cream are an interesting concept, but the review suggests that they may not be for everyone. While the idea of a cookie cone is exciting and unique, the reviewer found the cone to be a bit hard to bite and didn't particularly enjoy the flavor. They 

### Manually Curated
Ref: https://docs.llamaindex.ai/en/stable/examples/llama_dataset/ragdataset_submission_template/#1c-creating-a-labelledragdataset-from-scratch-with-manually-constructed-examples

In [58]:
response_curated_eval_dataset = response_evaluator.generate_curated_dataset(cfg)

2024-08-06 00:10:51.966 | INFO     | src.run.eval.response:generate_curated_dataset:124 - Persisting curated response eval dataset at data/005_use_smaller_embedding_model/response_curated_eval_dataset.json...


In [59]:
response_curated_eval_prediction_dataset = await response_curated_eval_dataset.amake_predictions_with(
    predictor=query_engine, batch_size=cfg.batch_size, show_progress=True
)

Batch processing of predictions:   0%|                                                                                                                                                                         | 0/4 [00:00<?, ?it/s]

> Top 10 nodes:
> [Node 57857698-df45-4408-b25f-dd047df5270c] [Similarity score:             0.414912] I would definitely come back here and try other things.
> [Node c5eca920-a5a1-40ed-8013-2b8106e8c539] [Similarity score:             0.413072] I would absolutely do it again.
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.410005] !! I might stalk them now
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.409612] Would try it again.
> [Node b72766fb-04d1-4c0f-bdd4-761aa9a19dd2] [Similarity score:             0.406728] I definitely recommend!
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.406132] But it didn't ruin my experience at all.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.405563] Definitely try this place for yourself
> [Node 5a9f9c31-9038-4eb7-962b-a7403aeb7e8e] [Similarity score:             0.403722] I would suggest Kinme instead for a sushi fix.
> [

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 57857698-df45-4408-b25f-dd047df5270c] [Similarity score:             0.414912] I would definitely come back here and try other things.
> [Node c5eca920-a5a1-40ed-8013-2b8106e8c539] [Similarity score:             0.413072] I would absolutely do it again.
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.410005] !! I might stalk them now
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.409612] Would try it again.
> [Node b72766fb-04d1-4c0f-bdd4-761aa9a19dd2] [Similarity score:             0.406728] I definitely recommend!
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.406132] But it didn't ruin my experience at all.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.405563] Definitely try this place for yourself
> [Node 5a9f9c31-9038-4eb7-962b-a7403aeb7e8e] [Similarity score:             0.403722] I would sug

> Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.54576] Would try it again.
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.527746] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.524924] I can't recommend it highly enough
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.519338] Definitely try this place for yourself
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.51875] But it didn't ruin my experience at all.
> [Node 2782ea50-c784-455e-afb2-531a4796f25c] [Similarity score:             0.512891] But I have become a fan.
> [Node d347960b-e423-426d-bfb7-d6f77a5715df] [Similarity score:             0.507216] I'm definitely coming back.
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.506812] !! I might stalk them now
> [Node f173320e-

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.54576] Would try it again.
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.527746] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.524924] I can't recommend it highly enough
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.519338] Definitely try this place for yourself
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.51875] But it didn't ruin my experience at all.
> [Node 2782ea50-c784-455e-afb2-531a4796f25c] [Similarity score:             0.512891] But I have become a fan.
> [Node d347960b-e423-426d-bfb7-d6f77a5715df] [Similarity score:             0.507216] I'm definitely coming back.
> [Node 89a125e9-05fa-4f33-b389-18bec55a6381] [Similarity score:             0.506812] !! I

> Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.516952] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.502909] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.50235] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.497705] We did not complain or say another word. We just packed up and left
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.493121] But it didn't ruin my experience at all.
> [Node 2782ea50-c784-455e-afb2-531a4796f25c] [Similarity score:             0.492954] But I have become a fan.
> [Node d347960b-e423-426d-bfb7-d6f77a5715df] [Similarity score:             0.490193] I'm definitely coming back.
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.487183] I can't r

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.516952] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.502909] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.50235] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node 000ca1c8-1417-44fd-bf40-ae4cf1532a7a] [Similarity score:             0.497705] We did not complain or say another word. We just packed up and left
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:             0.493121] But it didn't ruin my experience at all.
> [Node 2782ea50-c784-455e-afb2-531a4796f25c] [Similarity score:             0.492954] But I have become a fan.
> [Node d347960b-e423-426d-bfb7-d6f77a5715df] [Similarity score:             0.490193] I'm definitely coming back.
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity

> Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.512168] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.504235] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.504077] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.497485] I can't recommend it highly enough
> [Node 57857698-df45-4408-b25f-dd047df5270c] [Similarity score:             0.49515] I would definitely come back here and try other things.
> [Node c5eca920-a5a1-40ed-8013-2b8106e8c539] [Similarity score:             0.492839] I would absolutely do it again.
> [Node 037d2833-b692-4996-b951-310ca77c4853] [Similarity score:             0.487319] Great selections. I've literally been coming here for years.
> [Node ed1c88b0-f077-4678-92ab-a1488d013fbe] [Similarity score:          

DEBUG [llama_index.core.indices.utils] > Top 10 nodes:
> [Node 6b19d425-7802-4f59-92b9-1e275f106549] [Similarity score:             0.512168] Would try it again.
> [Node 82412639-bb22-49b4-a8e6-3ca388b8f98b] [Similarity score:             0.504235] Definitely try this place for yourself
> [Node 762f12d1-0837-4bc4-905c-934a437fec33] [Similarity score:             0.504077] More to try!

Thanks for the great service, Ardmore Pizza!
> [Node e7882cc9-17ce-4fd3-93ee-82395d5b77fb] [Similarity score:             0.497485] I can't recommend it highly enough
> [Node 57857698-df45-4408-b25f-dd047df5270c] [Similarity score:             0.49515] I would definitely come back here and try other things.
> [Node c5eca920-a5a1-40ed-8013-2b8106e8c539] [Similarity score:             0.492839] I would absolutely do it again.
> [Node 037d2833-b692-4996-b951-310ca77c4853] [Similarity score:             0.487319] Great selections. I've literally been coming here for years.
> [Node ed1c88b0-f077-4678-92ab-a14

In [60]:
response_curated_mean_scores_df, response_curated_deep_eval_df = response_evaluator.evaluate_labelled_rag_dataset(
    response_curated_eval_dataset,
    response_curated_eval_prediction_dataset,
    dataset_name="curated",
    judge_model=cfg.eval_cfg.response_eval_llm_model,
    cache_dp=cfg.notebook_cache_dp
)

  0%|                                                                                                                                                                                                          | 0/4 [00:00<?, ?it/s]

> Adding chunk: I can't recommend it highly enough


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I can't recommend it highly enough


> Adding chunk: !! I might stalk them now


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: !! I might stalk them now


...

DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: But it didn't ruin my experience at all.


> Adding chunk: I would definitely come back here and try other...


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I would definitely come back here and try other...


> Adding chunk: I would absolutely do it again.


DEBUG [llama_index.core.node_parser.node_utils] > Adding chunk: I would absolutely do it again.
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:12<00:00,  3.08s/it]


In [61]:
response_curated_mean_scores_df

rag                      base_rag
metrics                          
mean_correctness_score       1.75
mean_relevancy_score         0.00
mean_faithfulness_score      0.00

In [62]:
response_curated_deep_eval_df

query  \
0             What are key features of llama-agents?   
1  What are the two critical areas of RAG system ...   
2  What are the two main metrics used to evaluate...   
3  How does the MemoryCache project by Mozilla ut...   

                                              answer  relevancy_score  \
0  \nI'm not familiar with the term "llama-agents...              0.0   
1  \nI'm not able to answer that question as it d...              0.0   
2  \nI'm not sure I can provide a direct answer t...              0.0   
3  \nThe MemoryCache project by Mozilla is a dece...              0.0   

   correctness_score  faithfulness_score  \
0                1.0                 0.0   
1                1.0                 0.0   
2                1.0                 0.0   
3                4.0                 0.0   

                                            contexts  
0  [I can't recommend it highly enough, !! I migh...  
1  [More to try!\n\nThanks for the great service,...  
2  [We did not complain or say another word. We j...  
3  [!! I might stalk them now, I definitely recom...

#### Answers for target questions

In [62]:
from IPython.display import Markdown

In [53]:
from src.run.eval.manual_eval_dataset import MANUAL_EVAL_QA

In [65]:
for question, expected_answer in MANUAL_EVAL_QA:
    display(Markdown(f"\n\n### Question: {question}\n"))
    response = query_engine.query(question)
    display_response(response)



### Question: What are key features of llama-agents?


**`Final Response:`** Distributed Service-Oriented Architecture: every agent in LlamaIndex can be its own independently running microservice, orchestrated by a fully customizable LLM-powered control plane that routes and distributes tasks.

Communication via Standardized API Interfaces: interface between agents using a central control plane orchestrator. Pass messages between agents using a message queue.

Define Agentic and Explicit Orchestration Flows: developers have the flexibility to directly define the sequence of interactions between agents, or leave it up to an “agentic orchestrator” that decides which agents are relevant to the task.

Ease of Deployment: launch, scale, and monitor each agent and your control plane independently.

Scalability and Resource Management: use our built-in observability tools to monitor the quality and performance of the system and each individual agent service.


Sources:
- [Introducing llama-agents: A Powerful Framework for Building Production Multi-Agent AI Systems](https://www.llamaindex.ai/blog/introducing-llama-agents-a-powerful-framework-for-building-production-multi-agent-ai-systems)
- [LlamaIndex Newsletter 2024-07-02](https://www.llamaindex.ai/blog/llamaindex-newsletter-2024-07-02)





#### Referenced Paragraphs
Article: **Introducing llama-agents: A Powerful Framework for Building Production Multi-Agent AI Systems**

> ...Introducing llama-agents: A Powerful Framework for Building Production Multi-Agent AI Systems
We're excited to announce the alpha release of  llama-agents , a new open-source framework designed to simplify the process of building, iterating, and deploying multi-agent AI systems and turn your agents into production microservices. Whether you're working on complex question-answering systems, collaborative AI assistants, or distributed AI workflows, llama-agents provides the tools and structure you need to bring your ideas to life. Key Features of llama-agents Distributed Service Oriented Architecture:  every agent in LlamaIndex can be its own independently running microservice, orchestrated by a fully customizable LLM-powered control plane that routes and distributes tasks. Communication via standardized API interfaces:  interface between agents using a central control plane orchestrator. Pass messages between agents using a message queue. Define agentic and explicit orchestration flows:...

Article: **LlamaIndex Newsletter 2024-07-02**

> ...Blogpost ,  Tweet . create-llama  Integrated with LlamaCloud:  Streamline your LLM application data pipelines with create-llama, now integrated with LlamaCloud for faster setup and efficient system maintenance.  Tweet . ✨ Feature Releases and Enhancements: We have launched llama-agents - new alpha-release framework that enables multi-agent AI systems to go into production. It features a distributed, service-oriented architecture, communication through standard HTTP APIs, agentic orchestration of flows, and is designed for easy deployment, scalability, and observability.  ...



### Question: What are the two critical areas of RAG system performance that are assessed in the 'Evaluating RAG with LlamaIndex' section of the OpenAI Cookbook?


**`Final Response:`** The two critical areas of RAG system performance that are assessed in the 'Evaluating RAG with LlamaIndex' section of the OpenAI Cookbook are the Retrieval System and Response Generation.


Sources:
- [OpenAI Cookbook: Evaluating RAG systems](https://www.llamaindex.ai/blog/openai-cookbook-evaluating-rag-systems-fe393c61fb93)





#### Referenced Paragraphs
Article: **OpenAI Cookbook: Evaluating RAG systems**

> ...OpenAI Cookbook: Evaluating RAG systems
We’re excited to unveil our  OpenAI Cookbook , a guide to evaluating Retrieval-Augmented Generation (RAG) systems using LlamaIndex. We hope you’ll find it useful in enhancing the effectiveness of your RAG systems, and we’re thrilled to share it with you. The OpenAI Cookbook has three sections: Understanding Retrieval-Augmented Generation (RAG):  provides a detailed overview of RAG systems, including the various stages involved in building the RAG system. Building RAG with LlamaIndex:  Here, we dive into the practical aspects, demonstrating how to construct a RAG system using LlamaIndex, specifically applied to Paul Graham’s essay, utilizing the  VectorStoreIndex . Evaluating RAG with LlamaIndex:  The final section focuses on assessing the RAG system’s performance in two critical areas:  the Retrieval System  and  Response Generation. We use our unique synthetic dataset generation method,  generate_question_context_pairs  to conduct thorough evalu...



### Question: What are the two main metrics used to evaluate the performance of the different rerankers in the RAG system?


**`Final Response:`** The two main metrics used to evaluate the performance of the different rerankers in the RAG system are Hit Rate and Mean Reciprocal Rank (MRR).


Sources:
- [Boosting RAG: Picking the Best Embedding & Reranker models](https://www.llamaindex.ai/blog/boosting-rag-picking-the-best-embedding-reranker-models-42d079022e83)





#### Referenced Paragraphs
Article: **Boosting RAG: Picking the Best Embedding & Reranker models**

> ...Boosting RAG: Picking the Best Embedding & Reranker models
UPDATE : The pooling method for the Jina AI embeddings has been adjusted to use mean pooling, and the results have been updated accordingly. Notably, the  JinaAI-v2-base-en  with  bge-reranker-large now exhibits a Hit Rate of 0.938202 and an MRR (Mean Reciprocal Rank) of 0.868539 and with CohereRerank  exhibits a Hit Rate of 0.932584, and an MRR of 0.873689. When building a Retrieval Augmented Generation (RAG) pipeline, one key component is the Retriever. We have a variety of embedding models to choose from, including OpenAI, CohereAI, and open-source sentence transformers. Additionally, there are several rerankers available from CohereAI and sentence transformers. But with all these options, how do we determine the best mix for top-notch retrieval performance? How do we know which embedding model fits our data best? Or which reranker boosts our results the most? In this blog post, we’ll use the  Retrieval Evaluation  module fr...

> ...However, actual outcomes may differ based on data characteristics, dataset size, and other variables like chunk_size, similarity_top_k, and so on. The table below showcases the evaluation results based on the metrics of Hit Rate and Mean Reciprocal Rank (MRR): Analysis: Performance by Embedding: OpenAI : Showcases top-tier performance, especially with the  CohereRerank  (0.926966 hit rate, 0.86573 MRR) and  bge-reranker-large  (0.910112 hit rate, 0.855805 MRR), indicating strong compatibility with reranking tools. bge-large : Experiences significant improvement with rerankers, with the best results from  CohereRerank  (0.876404 hit rate, 0.822753 MRR). llm-embedder : Benefits greatly from reranking, particularly with  CohereRerank  (0.882022 hit rate, 0.830243 MRR), which offers a substantial performance boost. Cohere : Cohere’s latest v3.0 embeddings outperform v2.0 and, with the integration of native CohereRerank, significantly improve its metrics, boasting a 0.88764 hit rate and a 0...



### Question: How does the MemoryCache project by Mozilla utilize PrivateGPT_AI and LlamaIndex to enhance personal knowledge management while maintaining privacy? Provide a brief overview of the project and its key features.


**`Final Response:`** The MemoryCache project by Mozilla utilizes PrivateGPT_AI and LlamaIndex to enhance personal knowledge management while maintaining privacy by integrating large language models with private data sources. This project allows users to store and query their personal knowledge base, including documents, notes, and other information, while ensuring the security and control of their data. The key features of the MemoryCache project include:

1. Integration with PrivateGPT_AI: The project utilizes PrivateGPT_AI, a large language model, to generate answers and provide insights from the user's personal knowledge base.
2. LlamaIndex: The project uses LlamaIndex, a framework for building generative AI applications, to connect the user's private data sources with the large language model, enabling the generation of answers and insights.
3. Data encryption: The project ensures the security of the user's data by encrypting it, making it difficult for unauthorized access.
4. Control over data: The user has control over their data, allowing them to decide what information is shared and with whom.
5. Query interface: The project provides a query interface that allows users to search and retrieve information from their personal knowledge base.

By utilizing PrivateGPT_AI and LlamaIndex, the MemoryCache project enables users to manage their personal knowledge base while maintaining privacy and control over their data.


Sources:
- [Build a ChatGPT with your Private Data using LlamaIndex and MongoDB](https://www.llamaindex.ai/blog/build-a-chatgpt-with-your-private-data-using-llamaindex-and-mongodb-b09850eb154c)

### Error Analysis

In [55]:
response_curated_eval_dataset_dict = dict()
for example in response_curated_eval_dataset.examples:
    response_curated_eval_dataset_dict[example.query] = {
        "reference_answer": example.reference_answer,
        "reference_contexts": example.reference_contexts,
    }

In [56]:
response_curated_deep_eval_df.sort_values(['relevancy_score', 'correctness_score', 'faithfulness_score'])

query  \
3  How does the MemoryCache project by Mozilla ut...   
0             What are key features of llama-agents?   
1  What are the two critical areas of RAG system ...   
2  What are the two main metrics used to evaluate...   

                                              answer  relevancy_score  \
3  \nThe MemoryCache project by Mozilla utilizes ...              1.0   
0  \n\nDistributed Service-Oriented Architecture:...              1.0   
1  \n\nThe two critical areas of RAG system perfo...              1.0   
2  \n\nThe two main metrics used to evaluate the ...              1.0   

   correctness_score  faithfulness_score  \
3                4.0                 1.0   
0                NaN                 1.0   
1                NaN                 1.0   
2                NaN                 1.0   

                                            contexts  
3  [Build a ChatGPT with your Private Data using ...  
0  [Introducing llama-agents: A Powerful Framewor...  
1  [OpenAI Cookbook: Evaluating RAG systems\nWe’r...  
2  [Boosting RAG: Picking the Best Embedding & Re...

In [57]:
response_curated_eval_irrelevance_df = (
    response_curated_deep_eval_df
    .loc[lambda df: df['relevancy_score'].lt(1)]
    .sort_values(['relevancy_score', 'correctness_score', 'faithfulness_score'])
)

for i, row in response_curated_eval_irrelevance_df.reset_index(drop=True).iterrows():
    print(f"\n\n==============Error #{i+1}===============\n\n")
    print(f"Query:\n{row.query}\n")
    contexts = '\n\n'.join(row.contexts)
    print(f"Context:\n{contexts}\n")
    print(f"Answer:\n{row.answer}\n----\n")
    expected = response_curated_eval_dataset_dict.get(row.query)
    if not expected:
        logger.error(f"Could not find query {row.query} in synthetic_response_eval_dataset_dict!")
        continue
    expected_answer = expected['reference_answer']
    print(f"Expected Answer:\n{expected_answer}\n")
    expected_contexts = expected['reference_contexts']
    print(f"Expected Contexts:\n{expected_contexts}\n")

# Persist run metadata

In [63]:
from src.run.utils import parse_collect_log, flatten_dict

In [64]:
collect_info = parse_collect_log(collect_fp)

In [65]:
if ARGS.LOG_TO_MLFLOW:
    import mlflow

    logger.info("Logging [COLLECT] info to MLflow...")
    mlflow.log_params(collect_info)
    logger.info("Logging config to MLflow...")
    mlflow.log_params(flatten_dict(cfg.model_dump(), "cfg", sep='.'))
    logger.info(f"Logging Retrieval Synthetic Eval Results to MLflow...")
    retrieval_evaluator.log_to_mlflow(cfg)
    logger.info(f"Logging Response Eval Results to MLflow...")
    response_evaluator.log_to_mlflow(
        cfg,
        'synthetic',
        response_synthetic_mean_scores_df,
        response_synthetic_deep_eval_df
    )
    response_evaluator.log_to_mlflow(
        cfg,
        'curated',
        response_curated_mean_scores_df,
        response_curated_deep_eval_df
    )

2024-08-06 00:11:38.355 | INFO     | __main__:<module>:4 - Logging [COLLECT] info to MLflow...
2024-08-06 00:11:38.394 | INFO     | __main__:<module>:6 - Logging config to MLflow...
/home/dvquys/frostmourne/study/vietai-genai03/final-project/review-rec-bot/.venv/lib/python3.11/site-packages/pydantic/main.py:364: UserWarning: Pydantic serializer warnings:
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  Expected `int` but got `str` - serialized value may not be as expected
  return self.__pydantic_serializer__.to_python(
2024-08-06 00:11:38.442 | INFO     | __main__:<module>:8 - Logging Retrieval Synthetic Eval Results to MLflow...
2024-08-06 00:11:39.556 | INFO     | __main

# Clean up

In [66]:
if ARGS.LOG_TO_MLFLOW:
    mlflow.end_run()

# Archive